## Preprocess Data
This part involves:
- Removing all NAN values/null or empty values
- Scaling the data to be normal
- Spliting the data into x, the parameters for training, and y, the output the model has to give.

Here we are reading from the csv and removing all rows with empty values

In [1]:
import pandas as pd

data = pd.read_csv('data/pulsar_data_train.csv')
data = data.dropna()

Before continuing you should always check if the data is good enough to have a model trained on. To get a good model usually a dataset with around 10,000 rows is required depending on the complexity of the columns.

Since we are trying to predict pulsars with 8 columns of complex mathematical values (excluding output column) we should aim for some where around 10K rows.

In [2]:
data.shape # this will show the number of rows and columns in the dataset (rows, columns)

(9273, 9)

Now that we have verified that we have rows that are close to 10K we can continue with standardising the data

This can be done with using sklearn's StandardScaler module which will scale your data for you. Here we are fitting the StandardScaler to our current dataset excluding the output column and then creating a new variable that will hold our scaled values to make sure we don't accidently modify the dataset.

In [3]:
from sklearn.preprocessing import StandardScaler

scaler = StandardScaler()
scaler.fit(data.drop('target_class', axis=1))
scaled_features = scaler.transform(data.drop('target_class', axis=1))

Now that we have scaled the data we can split our data into x and y, where x will hold all the scaled columns except the targer column and y will only be the target column

In [4]:
x = pd.DataFrame(scaled_features, columns=data.columns[:-1])
y = data['target_class']

We can see a before and after for our data, before being when the data isn't scaled and after being when the data has been scaled.

Before

In [5]:
data.iloc[:, :8].head()

Mean of the integrated profile  \
0                      121.156250   
1                       76.968750   
2                      130.585938   
4                       84.804688   
7                      109.406250   

   Standard deviation of the integrated profile  \
0                                     48.372971   
1                                     36.175557   
2                                     53.229534   
4                                     36.117659   
7                                     55.912521   

   Excess kurtosis of the integrated profile  \
0                                   0.375485   
1                                   0.712898   
2                                   0.133408   
4                                   0.825013   
7                                   0.565106   

   Skewness of the integrated profile  Mean of the DM-SNR curve  \
0                           -0.013165                  3.168896   
1                            3.388719                  2.399666   
2                           -0.297242                  2.743311   
4                            3.274125                  2.790134   
7                            0.056247                  2.797659   

   Standard deviation of the DM-SNR curve  \
0                               18.399367   
1                               17.570997   
2                               22.362553   
4                               20.618009   
7                               19.496527   

   Excess kurtosis of the DM-SNR curve  Skewness of the DM-SNR curve  
0                             7.449874                     65.159298  
1                             9.414652                    102.722975  
2                             8.508364                     74.031324  
4                             8.405008                     76.291128  
7                             9.443282                     97.374578

After

In [6]:
x.head()

Mean of the integrated profile  \
0                        0.390208   
1                       -1.330153   
2                        0.757336   
3                       -1.025075   
4                       -0.067257   

   Standard deviation of the integrated profile  \
0                                      0.274138   
1                                     -1.524637   
2                                      0.990345   
3                                     -1.533176   
4                                      1.386010   

   Excess kurtosis of the integrated profile  \
0                                  -0.097154   
1                                   0.217862   
2                                  -0.323162   
3                                   0.322535   
4                                   0.079880   

   Skewness of the integrated profile  Mean of the DM-SNR curve  \
0                           -0.286951                 -0.321398   
1                            0.254214                 -0.347241   
2                           -0.332141                 -0.335696   
3                            0.235985                 -0.334123   
4                           -0.275909                 -0.333870   

   Standard deviation of the DM-SNR curve  \
0                               -0.405724   
1                               -0.448114   
2                               -0.202916   
3                               -0.292190   
4                               -0.349579   

   Excess kurtosis of the DM-SNR curve  Skewness of the DM-SNR curve  
0                            -0.192994                     -0.375589  
1                             0.238857                     -0.028295  
2                             0.039658                     -0.293563  
3                             0.016941                     -0.272670  
4                             0.245149                     -0.077743

Now we can split our training data into 2 parts, training and testing data. The training data will be used to train the model and the testing data will be used to evaluate it's accuracy.

In [7]:
from sklearn.model_selection import train_test_split

x_train, x_test, y_train, y_test = train_test_split(x, y, test_size=0.2, random_state=42)

# x_train is the training data set with features
# x_test is the test data set with features
# y_train is the training data set with labels
# y_test is the test data set with labels

## Model
This part involves:
- Selecting an appropriat model
- Training the model on the dataset
- Loading the testing dataset to test the model's accuracy
- Fine tuning the model further
- Using custom data to get outputs

Since we are classifing our end results into 1's and 0's where a 1 is a pulsar and a 0 is not a pulsar we do not need to use a Neural Network or any complex model, instead we can sklearn's RandomForestClassifier.

A RandomForestClassifier is a model that is full of a pre defined number of DesicionTrees. A DesicionTree is a model that will look through your dataset to construct a tree.
This Tree wil have a root node which is the most important classification it will make, then it will branch off into leaves which have more classifications until it reaches the end where it will output a desicion. Each level in the tree will consist of only one column. So the root node will use a column to make a desicion, then the next level will use the 2nd most important column and so and so forth until nothing is left.

![image](https://www.mastersindatascience.org/wp-content/uploads/sites/54/2022/05/tree-graphic.jpg)

A RandomTreeClassifier takes random batches of your data and then creates a set number of trees from these batches. It will then feed any data you give into these trees and give the most recurring output

After we make our random tree model we can even visualize it using a library called matplotlib

Here we will import the RandomForestClassifier and then fit it to our training x and y

In [8]:
from sklearn.ensemble import RandomForestClassifier

model = RandomForestClassifier(n_estimators=100, random_state=42)
# n_estimators is the number of trees in the forest
# random_state is the seed used by the random number generator

model.fit(x_train, y_train)

RandomForestClassifier(random_state=42)

Now lets use the testing x and y data to score the model

In [9]:
model.score(x_test, y_test)

0.9795148247978437

This shows that our model has an accuracy of 97.9% with respect to the data

In [10]:
import matplotlib.pyplot as plt
from sklearn import tree

feature_names = x.columns
target_name = y.unique().astype(str)

fig, axes = plt.subplots(nrows = 1,ncols = 1,figsize = (16,16), dpi=800)
tree.plot_tree(model.estimators_[0], feature_names= feature_names, class_names=target_name, filled=True)

[Text(0.6745844822303921, 0.9736842105263158, 'Standard deviation of the DM-SNR curve <= 0.855\ngini = 0.179\nsamples = 4693\nvalue = [6683, 735]\nclass = 0.0'),
 Text(0.49786177491830064, 0.9210526315789473, 'Excess kurtosis of the integrated profile <= 0.676\ngini = 0.057\nsamples = 3956\nvalue = [6083, 184]\nclass = 0.0'),
 Text(0.5862231285743464, 0.9473684210526316, 'True  '),
 Text(0.3192529616013072, 0.868421052631579, 'Skewness of the integrated profile <= -0.207\ngini = 0.028\nsamples = 3880\nvalue = [6067, 88]\nclass = 0.0'),
 Text(0.08231209150326797, 0.8157894736842105, 'Standard deviation of the DM-SNR curve <= -0.206\ngini = 0.011\nsamples = 2636\nvalue = [4134, 24]\nclass = 0.0'),
 Text(0.0196078431372549, 0.7631578947368421, 'Excess kurtosis of the DM-SNR curve <= 0.806\ngini = 0.004\nsamples = 1989\nvalue = [3125, 7]\nclass = 0.0'),
 Text(0.013071895424836602, 0.7105263157894737, 'gini = 0.0\nsamples = 1510\nvalue = [2369, 0]\nclass = 0.0'),
 Text(0.026143790849673203,

Now we can load another csv that containes empty target value (pulsar or not) and fill it with the data our model gives

In [12]:
test_data = pd.read_csv('data/pulsar_data_test.csv')
x = test_data.drop('target_class', axis=1)

test_data['target_class'] = model.predict(x)

filtered_data = test_data[test_data['target_class'] == 1]
filtered_data

Mean of the integrated profile  \
1                          75.585938   
18                         99.304688   
19                        105.882812   
20                         91.562500   
24                         80.156250   
...                              ...   
5348                       95.726562   
5350                      107.171875   
5352                       12.132812   
5362                       92.718750   
5364                       93.828125   

      Standard deviation of the integrated profile  \
1                                        34.386254   
18                                       46.185522   
19                                       36.696309   
20                                       36.637103   
24                                       37.580629   
...                                            ...   
5348                                     39.414408   
5350                                     38.581308   
5352                                     29.895749   
5362                                     43.978499   
5364                                     51.244986   

      Excess kurtosis of the integrated profile  \
1                                      2.025498   
18                                     0.641643   
19                                     0.530195   
20                                     0.627966   
24                                     0.816715   
...                                         ...   
5348                                   0.608902   
5350                                   0.497571   
5352                                   6.583985   
5362                                   0.582996   
5364                                   0.387653   

      Skewness of the integrated profile  Mean of the DM-SNR curve  \
1                               8.652913                  3.765050   
18                              0.709734                  2.031773   
19                              1.630786                  2.385452   
20                              1.989284                  1.429766   
24                              2.292702                  2.527592   
...                                  ...                       ...   
5348                            1.292570                  2.249164   
5350                            1.307112                  2.754181   
5352                           45.411825                 99.940635   
5362                            0.684253                  2.190635   
5364                            0.011425                  1.926421   

      Standard deviation of the DM-SNR curve  \
1                                  21.897049   
18                                 17.679675   
19                                 14.092365   
20                                 12.009719   
24                                 16.551533   
...                                      ...   
5348                               17.351321   
5350                               18.046756   
5352                               71.390822   
5362                               20.620851   
5364                               19.543869   

      Excess kurtosis of the DM-SNR curve  Skewness of the DM-SNR curve  \
1                                7.048189                     55.878791   
18                              10.741453                    124.274283   
19                               9.012541                    110.830217   
20                              13.040351                    214.609712   
24                               8.936706                           NaN   
...                                   ...                           ...   
5348                             8.792675                     86.536264   
5350                             8.760541                     91.122246   
5352                             0.243151                     -0.678561   
5362                            10.083348                    104.968732   
5364                